# 环境准备

In [1]:
!unzip ./PaddleDetection.zip
!mv ./PaddleDetection-release-2.7 ./PaddleDetection

Archive:  ./PaddleDetection.zip
61cef7a7fe45c009fca76a13c47dcc516d535df9
   creating: PaddleDetection-release-2.7/
   creating: PaddleDetection-release-2.7/.github/
   creating: PaddleDetection-release-2.7/.github/ISSUE_TEMPLATE/
  inflating: PaddleDetection-release-2.7/.github/ISSUE_TEMPLATE/1_bug-report.yml  
  inflating: PaddleDetection-release-2.7/.github/ISSUE_TEMPLATE/2_feature-request.yml  
  inflating: PaddleDetection-release-2.7/.github/ISSUE_TEMPLATE/3_documentation-issue.yml  
  inflating: PaddleDetection-release-2.7/.github/ISSUE_TEMPLATE/4_ask-a-question.yml  
  inflating: PaddleDetection-release-2.7/.github/ISSUE_TEMPLATE/5_others.yml  
  inflating: PaddleDetection-release-2.7/.gitignore  
  inflating: PaddleDetection-release-2.7/.pre-commit-config.yaml  
  inflating: PaddleDetection-release-2.7/.style.yapf  
  inflating: PaddleDetection-release-2.7/.travis.yml  
   creating: PaddleDetection-release-2.7/.travis/
   creating: PaddleDetection-release-2.7/.travis/codestyle/


# 数据
该数据集为足球比赛的数据集，其中具体文件说明如下： 

trian：文件夹内包含所有训练集的文件，形如SNMOT-060

 ----SNMOT-060：文件夹内包含该视频相关的

 ----det:dectection的标签，在本任务中不使用，不做解释

 ----gt：

 ----gt.txt：目标追踪的标签信息（具体内容在后边解释）
 
 ----img1：其中是该视频按帧抽取的所图片，文件名为帧数

 ----gameinfo.ini：该视频的相关信息，主要是该视频中trackletID到label的映射关系

 ----seqinfo.ini：该视频的相关信息，主要是视频的像素长宽以及视频的帧率和帧数

gt.txt中每一列的含义：

(frame_id) (trackletID) (bb_left) (bb_top) (width) (height) (mark) (-1) (-1) (-1)

- frame_id: 帧序号
- trackletID: 追踪目标的id
- bb_left检 测框左上角坐标的x
- bb_top: 检测框左上角坐标的y
- width: 检测框的宽度
- height: 检测框的高度
- mark: 当前这一行标签是否使用，当为1时表示使用，为0时表示不使用

最后三列设置为-1，在本任务中不使用。

In [3]:
!mkdir -p work/dataset/IKCEST/images
!unzip data/data272560/train.zip -d work/dataset/IKCEST/images
!unzip data/data272560/test.zip -d work/dataset/IKCEST/images

Archive:  data/data272560/train.zip
   creating: work/dataset/IKCEST/images/train/
   creating: work/dataset/IKCEST/images/train/SNMOT-060/
   creating: work/dataset/IKCEST/images/train/SNMOT-060/gt/
  inflating: work/dataset/IKCEST/images/train/SNMOT-060/gt/gt.txt  
   creating: work/dataset/IKCEST/images/train/SNMOT-060/det/
  inflating: work/dataset/IKCEST/images/train/SNMOT-060/det/det.txt  
  inflating: work/dataset/IKCEST/images/train/SNMOT-060/seqinfo.ini  
  inflating: work/dataset/IKCEST/images/train/SNMOT-060/gameinfo.ini  
   creating: work/dataset/IKCEST/images/train/SNMOT-060/img1/
  inflating: work/dataset/IKCEST/images/train/SNMOT-060/img1/000001.jpg  
  inflating: work/dataset/IKCEST/images/train/SNMOT-060/img1/000002.jpg  
  inflating: work/dataset/IKCEST/images/train/SNMOT-060/img1/000003.jpg  
  inflating: work/dataset/IKCEST/images/train/SNMOT-060/img1/000004.jpg  
  inflating: work/dataset/IKCEST/images/train/SNMOT-060/img1/000005.jpg  
  inflating: work/dataset/IK

文件目录如下： \
IKCEST\
   $~~~~~~~~$|————images \
   $~~~~~~~~~~~~~~~~~~~~~~~~~~$ └——————train \
   $~~~~~~~~~~~~~~~~~~~~~~~~~~$ └——————test
           
对文件进行处理，处理后的文件目录如下：\
IKCEST\
   $~~~~~~~~$|————images \
   $~~~~~~~~$|$~~~~~~~~~~~~~~~~$ └——————train \
   $~~~~~~~~$|$~~~~~~~~~~~~~~~~$ └——————test\
   $~~~~~~~$└————labels_with_ids \
   $~~~~~~~~~~~~~~~~~~~~~~~~~~$└——————train \
详细参考[MOT数据准备文档](https://github.com/PaddlePaddle/PaddleDetection/blob/develop/docs/tutorials/data/PrepareMOTDataSet.md)\
其中提到的label_list.txt已经生成完成，也可以根据自己的策略来生成，注意class_label文件在work/dataset/label_list.txt\
由于本任务的测评指标不计算label，所以不做着重处理。

In [4]:
import os.path as osp
import os

def mkdirs(d):
    if not osp.exists(d):
        os.makedirs(d)

def getid_dict(file_path):
    result = {}

    with open(file_path, 'r') as file:
        lines = file.readlines()

    for line in lines:
        line = line.strip()
        if line.startswith("trackletID"):
            key_value = line.split("=")
            tracklet_id = int(key_value[0].split("_")[1])
            value = key_value[1].strip()

            if "ball" in value:
                value = "ball"
            if "other" in value:
                value = "other"
            result[tracklet_id] = value
    return result

In [7]:

import numpy as np


MOT_data = 'IKCEST' # Name of the dataset or folder


seq_root = './work/dataset/{}/images/train'.format(MOT_data)
label_root = './work/dataset/{}/labels_with_ids/train'.format(MOT_data)
label_path = './work/dataset/label_list.txt'
cname2cid = {}
with open(label_path, 'r') as fr:
    label_id = 0
    for line in fr.readlines():
        cname2cid[line.strip()] = label_id
        label_id += 1
# import pprint
# pprint.pprint(cname2cid)
mkdirs(label_root)
seqs = [s for s in os.listdir(seq_root)]

tid_curr = 1
tid_last = -1

for seq in seqs:
    seq_info = open(osp.join(seq_root, seq, 'seqinfo.ini')).read()
    seq_width = int(seq_info[seq_info.find('imWidth=') + 8:seq_info.find(
        '\nimHeight')])
    seq_height = int(seq_info[seq_info.find('imHeight=') + 9:seq_info.find(
        '\nimExt')])

    gt_txt = osp.join(seq_root, seq, 'gt', 'gt.txt')

    gameinfo_path = osp.join(seq_root, seq, 'gameinfo.ini')
    gameinfo = getid_dict(gameinfo_path)

    gt = np.loadtxt(gt_txt, dtype=np.float64, delimiter=',')
    seq_label_root = osp.join(label_root, seq, 'img1')
    mkdirs(seq_label_root)

    for gt_temp in gt:
        fid,tid, x, y, w, h, mark, _, _ ,_ = gt_temp
        if mark == 0 :
            continue
        fid = int(fid)
        tid = int(tid)
        label = cname2cid[gameinfo[tid]]
        if not tid == tid_last:
            tid_curr += 1
            tid_last = tid
        x += w / 2
        y += h / 2
        label_fpath = osp.join(seq_label_root, '{:06d}.txt'.format(fid))
        label_str = '{:d} {:d} {:.6f} {:.6f} {:.6f} {:.6f}\n'.format(label,
            tid_curr, x / seq_width, y / seq_height, w / seq_width,
            h / seq_height)
        with open(label_fpath, 'a') as f:
            f.write(label_str)
    print("create \"{}\" successfully!".format(seq_label_root))
print("create \"folder\" to \"{}\" successfully!".format(label_root))

create "./work/dataset/IKCEST/labels_with_ids/train/SNMOT-152/img1" successfully!
create "./work/dataset/IKCEST/labels_with_ids/train/SNMOT-076/img1" successfully!
create "./work/dataset/IKCEST/labels_with_ids/train/SNMOT-111/img1" successfully!
create "./work/dataset/IKCEST/labels_with_ids/train/SNMOT-105/img1" successfully!
create "./work/dataset/IKCEST/labels_with_ids/train/SNMOT-098/img1" successfully!
create "./work/dataset/IKCEST/labels_with_ids/train/SNMOT-156/img1" successfully!
create "./work/dataset/IKCEST/labels_with_ids/train/SNMOT-075/img1" successfully!
create "./work/dataset/IKCEST/labels_with_ids/train/SNMOT-158/img1" successfully!
create "./work/dataset/IKCEST/labels_with_ids/train/SNMOT-104/img1" successfully!
create "./work/dataset/IKCEST/labels_with_ids/train/SNMOT-164/img1" successfully!
create "./work/dataset/IKCEST/labels_with_ids/train/SNMOT-155/img1" successfully!
create "./work/dataset/IKCEST/labels_with_ids/train/SNMOT-169/img1" successfully!
create "./work/d

In [9]:
# 生成IKCEST.train文件并且复制到 image_lists下面
import glob
import os.path as osp
image_list = []
for seq in sorted(glob.glob('./work/dataset/IKCEST/images/train/*')):
    for image in glob.glob(osp.join(seq, "img1")+'/*.jpg'):
        image = image.replace('./work/dataset/','')
        image_list.append(image)
with open('IKCEST.train','w') as image_list_file:
    image_list_file.write(str.join('\n',image_list))
!mkdir -p ./work/dataset/image_lists && cp -r IKCEST.train ./work/dataset/image_lists

修改配置文件
添加在PaddleDetection/configs/datasets/mcmot.yml文件最后 \
同时修改PaddleDetection/configs/mot/mcfairmot/mcfairmot_dla34_30e_1088x608_visdrone_vehicle_bytetracker.yml文件\
或者参照该文件重新编写自己的配置文件
```
num_classes: 228

# for MCMOT training
TrainDataset:
  !MCMOTDataSet
    dataset_dir: ./work/dataset # 需要更改为自己对应的文件目录下
    image_lists: ['IKCEST.train']
    data_fields: ['image', 'gt_bbox', 'gt_class', 'gt_ide']
    label_list: ./work/dataset/label_list.txt

EvalMOTDataset:
  !MOTImageFolder
    dataset_dir: ./work/dataset
    data_root: IKCEST/images/test/
    keep_ori_im: False # set True if save visualization images or video, or used in DeepSORT
    anno_path: ./work/dataset/label_list.txt

# for MCMOT video inference
TestMOTDataset:
  !MOTImageFolder
    dataset_dir: ./work/dataset
    keep_ori_im: True # set True if save visualization images or video
    anno_path: ./work/dataset/label_list.txt

```

# 模型

## 模型结构

本任务的basleline采用PaddleDectection库中提供的多目标追踪的模型来实现该任务\
采用JDE的网络结构，主体网络采用Fairmot，网络结构如下：

<div align=center><img src="https://ai-studio-static-online.cdn.bcebos.com/976807c091614e1ab80c1b1d0f58ae2baf6fea63ac3841138f308d8eef3432c6" alt="description of image" width="600" height="500"><div>
    
特征提取网络使用的是CenterNet结构，基准网络使用DLA34，网络结构如下：
    
<div align=center><img src="https://ai-studio-static-online.cdn.bcebos.com/640309348b21474e8b181a2569586ef3c9d4813cb0564011baa0407fc31fcae1" alt="description of image" width="600" height="500"><div>
    
<div align=center><img src="https://ai-studio-static-online.cdn.bcebos.com/be379f43bf1443aca818da94ef80946e8025d9e590dc4e0aac0095f92d1c3001" alt="description of image" width="600" height="500"><div>


## 训练参数配置

在 PaddleDetection/configs/mot/mcfairmot/mcfairmot_dla34_30e_1088x608_visdrone_vehicle_bytetracker.yml 文件中修改模型参数

部分参数说明如下：
- pretrain_weights: #预训练参数，默认使用与paddle官方的训练参数，更改为自己已经训练过保存的参数可以继续训练模型
- FairMOT: #设置模型的相关组件，其中需要注意tracker需要选择支持多类别追踪的JDETracker
- JDETracker: #追踪模型的相关训练参数设置
- epoch: #训练轮数
- LearningRate: #学习率的相关参数设置
- OptimizerBuilder: #优化器相关设置

在 PaddleDetection/configs/runtime.yml 中修改训练参数

部分参数说明如下：
- save_dir: #模型参数保存的文件位置
- snapshot_epoch: #模型参数保存需要的轮次

以上参数根据自己的需求进行调整

在 PaddleDetection/configs/mot/fairmot/_base_/fairmot_reader_1088x608.yml 中修改
- batch_size: 
- worker_num: #需要修改为2,不然内存会不够


## 训练

In [20]:
# <!--训练-->
!python -m paddle.distributed.launch --log_dir=./mcfairmot_dla34_30e_1088x608_visdrone_vehicle_bytetracker/  --gpus 0 ./PaddleDetection/tools/train.py -c ./PaddleDetection/configs/mot/mcfairmot/mcfairmot_dla34_30e_1088x608_visdrone_vehicle_bytetracker.yml
# --log_dir:日志文件的目录;
# --gpus:使用gpu，若多卡训练则指定多张卡如：0,1,2;
# -c: 配置文件路径;
# 其他可配置参数在./PaddleDetection/tools/train.py文件中查看
# 已经提供了模型文件在output文件夹下

LAUNCH INFO 2024-08-28 21:46:33,716 -----------  Configuration  ----------------------
LAUNCH INFO 2024-08-28 21:46:33,716 auto_parallel_config: None
LAUNCH INFO 2024-08-28 21:46:33,716 auto_tuner_json: None
LAUNCH INFO 2024-08-28 21:46:33,716 devices: 0
LAUNCH INFO 2024-08-28 21:46:33,716 elastic_level: -1
LAUNCH INFO 2024-08-28 21:46:33,716 elastic_timeout: 30
LAUNCH INFO 2024-08-28 21:46:33,716 enable_gpu_log: True
LAUNCH INFO 2024-08-28 21:46:33,716 gloo_port: 6767
LAUNCH INFO 2024-08-28 21:46:33,716 host: None
LAUNCH INFO 2024-08-28 21:46:33,716 ips: None
LAUNCH INFO 2024-08-28 21:46:33,716 job_id: default
LAUNCH INFO 2024-08-28 21:46:33,716 legacy: False
LAUNCH INFO 2024-08-28 21:46:33,716 log_dir: ./mcfairmot_dla34_30e_1088x608_visdrone_vehicle_bytetracker/
LAUNCH INFO 2024-08-28 21:46:33,716 log_level: INFO
LAUNCH INFO 2024-08-28 21:46:33,716 log_overwrite: False
LAUNCH INFO 2024-08-28 21:46:33,716 master: None
LAUNCH INFO 2024-08-28 21:46:33,716 max_restart: 3
LAUNCH INFO 2024

## 评估

In [ ]:
# <!--评估-->  生成结果文件
!CUDA_VISIBLE_DEVICES=0 python ./PaddleDetection/tools/eval_mot.py -c ./PaddleDetection/configs/mot/mcfairmot/mcfairmot_dla34_30e_1088x608_visdrone_vehicle_bytetracker.yml  -o weights=./output/5.pdparams
# -o weights：需要加载的模型参数文件
# 输出的结果将保存在output/mot_results文件夹下
# 输出格式表示为frame_id, trackltid, bbox_left, bbox_top, bbox_width, bbox_height, score, cls_id, -1, -1